In [1]:
import sys
import os
from pathlib import Path
from dotenv import load_dotenv
import plotly.io as pio
# Add the src directory to the Python path
project_root = Path.cwd().parent.parent
if str(project_root) not in sys.path:
    sys.path.append(str(project_root))

# Load environment variables from .env file at the project root
load_dotenv(project_root / ".env")
pio.renderers.default = "notebook_connected"

from src.maritime_module.core.s57_data import ENCDataFactory, S57AdvancedConfig
from src.maritime_module.utils.port_utils import Boundaries, PortData
from src.maritime_module.utils.plot_utils import PlotlyChart

# Define paths for data and output

output_dir = Path.cwd() / 'output'
output_dir.mkdir(exist_ok=True)

# Define database file
gpkg_file = Path.cwd() / "output" / "us_enc_all.gpkg"

print(f"Output directory: {output_dir}")
print(f"GeoPackage file: {gpkg_file}")

Output directory: /home/vikont_tux/python_projects_wsl2/1_MaritimeModule_V1/docs/notebooks/output
GeoPackage file: /home/vikont_tux/python_projects_wsl2/1_MaritimeModule_V1/docs/notebooks/output/us_enc_all.gpkg


In [2]:
port  = PortData()
bbox = Boundaries()
port1 = port.get_port_by_name('Los Angeles')
port2 = port.get_port_by_name('San Francisco')
print(port.format_port_string(port1))
print(port.format_port_string(port2))
port_bbox = bbox.create_geo_boundary(geometries = [port1.geometry, port2.geometry],
                                     expansion=24,
                                     date_line=True)
port_bbox

2025-09-30 14:10:35,711 - src.maritime_module.utils.port_utils - INFO - Loaded 1 custom ports. Merging with standard ports.
LOS ANGELES, US (LAT: 33° 45.0' N  LONG: 118° 15.0' W)
SAN FRANCISCO, US (LAT: 37° 49.0' N  LONG: 122° 25.0' W)


geometry
0  POLYGON ((-117.85 33.35, -117.85 38.217, -122....

In [3]:
ply = PlotlyChart()
ply_fig = ply.create_base_map(mapbox_token="pk.eyJ1Ijoidmlrb250IiwiYSI6ImNtNHljdzQwbjBybWIybHNkZzhleXhqYXUifQ.Jz0cR4J6PdAnLutVBqj2WA")
ply.plotly_base_config(ply_fig)
port1_df = port.get_port_details_df(port1)
port2_df = port.get_port_details_df(port2)
ply.add_single_port_trace(ply_fig, port1, name=port1['PORT_NAME'], color='blue')
ply.add_single_port_trace(ply_fig, port2, name=port2['PORT_NAME'], color='red')
ply_fig.show()

In [4]:
ply.add_boundary_trace(ply_fig, port_bbox)
ply_fig.show()

In [5]:
gpkg_factory = ENCDataFactory(source=gpkg_file)
# 1. Filter to get the list of ENC names within the boundary
enc_names_in_boundary = gpkg_factory.get_encs_by_boundary(port_bbox.geometry.iloc[0])
# 2. Get the bounding box GeoDataFrame for only those filtered ENCs
enc_bbox_gdf = gpkg_factory.get_enc_bounding_boxes(enc_names_in_boundary)
ply.add_enc_bbox_trace(figure=ply_fig, bbox_df=enc_bbox_gdf, usage_bands=[1,2,3,4,5,6])
ply_fig.show()

2025-09-30 14:10:36,281 - src.maritime_module.core.s57_data - INFO - Source is a .gpkg file, initializing GPKGManager.
2025-09-30 14:10:36,282 - src.maritime_module.core.s57_data - INFO - Routes will be managed in: /home/vikont_tux/python_projects_wsl2/1_MaritimeModule_V1/docs/notebooks/output/maritime_routes.gpkg
2025-09-30 14:10:36,295 - src.maritime_module.core.s57_data - INFO - Successfully connected to GeoPackage 'us_enc_all.gpkg'
2025-09-30 14:10:36,297 - src.maritime_module.core.s57_data - INFO - Factory: Filtering ENCs by boundary...
2025-09-30 14:10:36,297 - src.maritime_module.core.s57_data - INFO - Factory: Getting ENC summary...
2025-09-30 14:10:36,410 - src.maritime_module.core.s57_data - INFO - Factory: Getting bounding boxes for 6369 ENCs...
2025-09-30 14:10:37,731 - src.maritime_module.core.s57_data - INFO - Factory: Getting bounding boxes for 54 ENCs...


In [6]:
from src.maritime_module.core.graph import BaseGraph

gpkg_bg = BaseGraph(data_factory=ENCDataFactory(source=gpkg_file),
                  graph_schema_name="graph")
grid = gpkg_bg.create_base_grid(port_boundary=port_bbox,
                              departure_port=port1,
                              arrival_port=port2,
                              layer_table="seaare",
                              reduce_distance_nm=0)
print(len(grid))
print(type(grid))
print(grid.keys())


2025-09-30 14:10:37,482 - src.maritime_module.core.s57_data - INFO - Source is a .gpkg file, initializing GPKGManager.
2025-09-30 14:10:37,483 - src.maritime_module.core.s57_data - INFO - Routes will be managed in: /home/vikont_tux/python_projects_wsl2/1_MaritimeModule_V1/docs/notebooks/output/maritime_routes.gpkg
2025-09-30 14:10:37,484 - src.maritime_module.core.s57_data - INFO - Successfully connected to GeoPackage 'us_enc_all.gpkg'
2025-09-30 14:10:37,499 - src.maritime_module.core.graph - INFO - Executing database-side grid creation for improved performance.
2025-09-30 14:10:37,500 - src.maritime_module.core.s57_data - INFO - Performing in-memory grid creation for file-based data source.
2025-09-30 14:10:40,934 - src.maritime_module.core.s57_data - INFO - Subtracting land areas from the grid...
2025-09-30 14:10:48,337 - src.maritime_module.core.graph - INFO - Database grid creation completed in 10.837s
2025-09-30 14:10:48,684 - src.maritime_module.core.graph - INFO - GeoJSON conve

In [7]:
ply_grid = ply.create_base_map(mapbox_token="pk.eyJ1Ijoidmlrb250IiwiYSI6ImNtNHljdzQwbjBybWIybHNkZzhleXhqYXUifQ.Jz0cR4J6PdAnLutVBqj2WA")
ply.plotly_base_config(ply_grid)
ply.add_grid_trace(ply_grid, grid_geojson=grid["main_grid"], color="red")
ply.add_grid_trace(ply_grid, grid_geojson=grid["extra_grids"], color="green")
ply.add_grid_trace(ply_grid, grid_geojson=grid["combined_grid"], color="blue")
ply_grid.show()

In [8]:
G = gpkg_bg.create_base_graph(grid["combined_grid"], 0.3,
                              keep_largest_component=True)

2025-09-30 14:10:51,244 - src.maritime_module.core.graph - INFO - Grid data parsing completed in 0.397s
2025-09-30 14:10:51,247 - src.maritime_module.core.graph - INFO - Starting subgraph creation for MultiPolygon with area 24.037849 deg²
2025-09-30 14:10:51,248 - src.maritime_module.core.graph - INFO - Creating grid: 995x969 = 964,155 potential points
2025-09-30 14:10:51,249 - src.maritime_module.core.graph - INFO - Using database-side graph creation for improved performance
2025-09-30 14:10:51,250 - src.maritime_module.core.graph - WARNING - Database-side graph creation failed: GPKGManager.create_grid_graph_nodes_and_edges() takes from 3 to 4 positional arguments but 5 were given. Falling back to memory-based approach.
2025-09-30 14:10:51,256 - src.maritime_module.core.graph - INFO - Mesh creation completed in 0.003s
2025-09-30 14:10:51,269 - src.maritime_module.core.graph - INFO - Point flattening completed in 0.012s
2025-09-30 14:10:51,411 - src.maritime_module.core.graph - INFO - 

In [9]:
output_file = output_dir / "base_graph_GPKG.gpkg"
gpkg_bg.save_graph_to_gpkg(G, output_file)

2025-09-30 14:11:19,948 - pyogrio._io - INFO - Created 359,814 records
2025-09-30 14:11:20,528 - src.maritime_module.core.graph - INFO - Saved 359,814 nodes to /home/vikont_tux/python_projects_wsl2/1_MaritimeModule_V1/docs/notebooks/output/base_graph_GPKG.gpkg in 2.610s
2025-09-30 14:11:53,215 - pyogrio._io - INFO - Created 1,430,984 records
2025-09-30 14:11:53,365 - src.maritime_module.core.graph - INFO - Saved 1,430,984 edges to /home/vikont_tux/python_projects_wsl2/1_MaritimeModule_V1/docs/notebooks/output/base_graph_GPKG.gpkg in 15.841s
2025-09-30 14:11:53,366 - src.maritime_module.core.graph - INFO - === Graph Save Operation Performance Summary ===
2025-09-30 14:11:53,367 - src.maritime_module.core.graph - INFO - Timing Metrics:
2025-09-30 14:11:53,367 - src.maritime_module.core.graph - INFO -   nodes_processing_time: 4.218s
2025-09-30 14:11:53,368 - src.maritime_module.core.graph - INFO -   nodes_save_time: 2.610s
2025-09-30 14:11:53,368 - src.maritime_module.core.graph - INFO - 

In [10]:
from src.maritime_module.core.pathfinding_lite import Route

route = Route(graph=G, data_manager=gpkg_factory.manager)
route_geometry, distance = route.base_route(
    departure_point=port1.geometry,
    arrival_point=port2.geometry
)

2025-09-30 14:11:54,165 - src.maritime_module.core.pathfinding_lite - INFO - Computing base route with Astar...
2025-09-30 14:11:54,166 - src.maritime_module.core.pathfinding_lite - INFO - Computing A* route...
2025-09-30 14:12:00,537 - src.maritime_module.core.pathfinding_lite - INFO - Mapped start point to graph node: (np.float64(-118.24700000000415), np.float64(33.7450000000002))
2025-09-30 14:12:00,539 - src.maritime_module.core.pathfinding_lite - INFO - Mapped end point to graph node: (np.float64(-122.41700000000036), np.float64(37.815000000002286))
2025-09-30 14:12:02,131 - src.maritime_module.core.pathfinding_lite - INFO - Successfully computed route with 1149 nodes.
2025-09-30 14:12:02,133 - src.maritime_module.core.pathfinding_lite - INFO - Route computed successfully. Total distance: 377.51 nautical miles.


In [11]:
ply_route = ply.create_base_map(mapbox_token="pk.eyJ1Ijoidmlrb250IiwiYSI6ImNtNHljdzQwbjBybWIybHNkZzhleXhqYXUifQ.Jz0cR4J6PdAnLutVBqj2WA")
ply.plotly_base_config(ply_route)
ply.add_route_trace(figure=ply_route,
                    line=route_geometry,
                    name="Base Route")
ply.add_single_port_trace(ply_route, port1, name=port1['PORT_NAME'], color='blue')
ply.add_single_port_trace(ply_route, port2, name=port2['PORT_NAME'], color='red')
ply_route.show()

In [12]:
gpkg_factory.save_route(route_geom=route_geometry,
                      route_name= "base_route_GPKG",
                      table_name= "base_route_table",
                      overwrite= True)

2025-09-30 14:12:02,519 - src.maritime_module.core.s57_data - INFO - Route 'base_route_GPKG' saved successfully to GeoPackage.
